In [71]:
from shapely.geometry import Point
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import folium
from folium.plugins import FloatImage
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster
from folium import IFrame
import time
import numpy as np

In [72]:
ntests = pd.read_csv('../data/Cleaned data/nuclear_test_coordinates.csv')
ntests.head()

STATE TESTTYPE  ID# SERIES      SHOT       Date       YEAR MONTH  DAY  \
0   China  Nuclear   26    NaN       NaN   2/2/1979  X    1979   FEB    2   
1   China  Nuclear   40    NaN       NaN  11/2/1992  X    1992   NOV    2   
2   China  Nuclear   46    NaN       NaN   6/8/1996  S    1996   JUN    8   
3   China  Nuclear   47    NaN       NaN   6/8/1996  SS   1996   JUN    8   
4  France  Nuclear   20   1966  Ganymede  7/21/1966  X    1966   JUL   21   

      TIME  ... CRATER (M)  VENT  DEVICE WARHEAD SPONSOR    R    N  \
0      NaN  ...        NaN   NaN     NaN     NaN     NaN  NaN  NaN   
1      NaN  ...        NaN   NaN     NaN     NaN     NaN  NaN  NaN   
2  55:57.9  ...        NaN   NaN     NaN     NaN     NaN  NaN  NaN   
3  55:57.9  ...        NaN   NaN     NaN     NaN     NaN  NaN  NaN   
4    12:00  ...        NaN   NaN      ND   AN-22     NaN  NaN  NaN   

      SOURCES                                              LINKS Location_Type  
0           e  https://foreignpolicy.com/2019/09/22/blast-fro...   Underground  
1           e  https://foreignpolicy.com/2019/09/22/blast-fro...   Underground  
2  1, 2, b, c  https://foreignpolicy.com/2019/09/22/blast-fro...   Underground  
3     1, 2, b  https://foreignpolicy.com/2019/09/22/blast-fro...   Underground  
4     2, 3, 5  https://foreignpolicy.com/2019/09/22/blast-fro...   Atmospheric  

[5 rows x 36 columns]

In [73]:
conditions = [
    ntests['STATE'] == 'China',
    ntests['STATE'] == 'France',
    ntests['STATE'] == 'United Kingdom',
    ntests['STATE'] == 'United States',
    ntests['STATE'] == 'North Korea',
    ntests['STATE'] == 'India',
    ntests['STATE'] == 'Pakistan',
    ntests['STATE'] == 'Russia/USSR',
    ntests['STATE'] == 'Unknown (Likely Israel)'
    ]

values = ['darkred','lightblue','darkblue','cadetblue','darkgreen','orange','green','red','gray']

ntests['color'] = np.select(conditions, values)

In [74]:
geometry = [Point(xy) for xy in zip(ntests.LONG, ntests.LAT)]
ntest_geo = gpd.GeoDataFrame(ntests, crs="EPSG:3857", geometry=geometry)

In [75]:
ntest_map = folium.Map(location = [0, 0], zoom_start = 1)
folium.TileLayer('cartodbpositron').add_to(ntest_map)

In [76]:
marker_cluster = MarkerCluster().add_to(ntest_map)

for row_index, row_values in ntest_geo.iterrows():
    state = row_values['STATE']
    date = str(row_values['Date'])
    kt = str(row_values['YIELD KT'])
    where = row_values['Location_Type']
    html="""
        <h3>{country}</h3>
        Date of test: {when}<br>
        Test type: {location}<br>
        Test yield: {boom} kilotons        
        """
    html = html.format(country=state, when=date, location=where, boom=kt)
    iframe = folium.IFrame(html=html, width=300, height=150)
    pop = folium.Popup(iframe, max_width=2650)
    loc = [row_values['LAT'], row_values['LONG']]
    marker = folium.Marker(
        location = loc,
        icon = folium.Icon(color=row_values['color'],icon="bullseye", prefix='fa'),
#        radius=100,
        popup = pop,
        fill=True,
        color=row_values['color'])
    
    marker.add_to(marker_cluster)
    
#    marker.add_to(ntest_map)
url = ('https://raw.githubusercontent.com/d-bowen/d-bowen.github.io/main/media/detonations_legend.PNG')
folium.plugins.FloatImage(url, bottom=85, left=75).add_to(ntest_map)

ntest_map


In [77]:
ntest_map.save('../maps/nuclear_tests.html')